In [202]:
import random
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

from matplotlib import pyplot as plt
import seaborn as sns
import pandas_profiling
import matplotlib
import matplotlib.pyplot as plt # for plotting
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
color = sns.color_palette()
import plotly.offline as py
py.init_notebook_mode(connected=True)
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.offline as offline
offline.init_notebook_mode()

from sklearn.ensemble import (RandomForestClassifier, AdaBoostClassifier, 
                              GradientBoostingClassifier, ExtraTreesClassifier)
import lightgbm as lgb
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression

from sklearn.neural_network import MLPClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier

from sklearn.cross_validation import KFold
# from plotly import tools
# import plotly.tools as tls
# import squarify
# from mpl_toolkits.basemap import Basemap
# from numpy import array
# from matplotlib import cm

# from sklearn import preprocessing
# # Supress unnecessary warnings so that presentation looks clean
# import warnings
# warnings.filterwarnings("ignore")

# # Print all rows and columns
# pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

In [3]:
import os
input_files = os.listdir("/Users/imac/.kaggle/competitions/home-credit-default-risk")
print(input_files)
for filename in input_files:
    locals()[filename.rstrip('.zip')] = pd.read_csv(f'/Users/imac/.kaggle/competitions/home-credit-default-risk/{filename}')

['.DS_Store', 'application_test.csv.zip', 'application_train.csv.zip', 'bureau.csv.zip', 'bureau_balance.csv.zip', 'credit_card_balance.csv.zip', 'installments_payments.csv.zip', 'POS_CASH_balance.csv.zip', 'previous_application.csv.zip', 'sample_submission.csv.zip']


In [203]:
application_train = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/application_train.csv.zip')
application_test = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/application_test.csv.zip')



In [14]:
POS_CASH_balance = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/POS_CASH_balance.csv.zip')
bureau_balance = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/bureau_balance.csv.zip')
previous_application = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/previous_application.csv.zip')
installments_payments = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/installments_payments.csv.zip')
credit_card_balance = pd.read_csv('/Users/imac/.kaggle/competitions/home-credit-default-risk/credit_card_balance.csv.zip')


In [204]:

# categoricalize
categorical_columns = ['NAME_CONTRACT_TYPE',
                       'CODE_GENDER',
                       'FLAG_OWN_CAR',
                       'FLAG_OWN_REALTY',
                       'NAME_TYPE_SUITE',
                       'NAME_INCOME_TYPE',
                       'NAME_EDUCATION_TYPE',
                       'NAME_FAMILY_STATUS',
                       'NAME_HOUSING_TYPE',
                       'OCCUPATION_TYPE',
                       'WEEKDAY_APPR_PROCESS_START',
                       'ORGANIZATION_TYPE',
                       'FONDKAPREMONT_MODE',
                       'HOUSETYPE_MODE',
                       'WALLSMATERIAL_MODE',
                       'EMERGENCYSTATE_MODE']

for column in categorical_columns:
    application_train[column] = application_train[column].astype('category')
    application_test[column] = application_test[column].astype('category')


In [5]:
pandas_profiling.ProfileReport(application_train)

# Итак План действий:
   1. Нужно убрать признаки которые сильно корелируют между собой
   2. Заполнить пропуски в оставшихся данных(Или убрать признаки)
   3. Запустить LGBM  и отобрать топ важных признаков(Первый Бейзлайн)
   4. Сгенерировать новые признаки на основе важных(MeanEncoding и тд)
   5. Построить на новых признаках несколько разных моделей
   6. Сделать Ансабль моделей и за сабмитить

In [205]:
input_columns = application_train.columns
input_columns = input_columns[input_columns != 'TARGET']
target_column = 'TARGET'

X = application_train[input_columns]
X_Full = pd.concat([X,application_test])
Y_TRAIN = application_train[target_column]
idx_split = X.shape[0]

In [212]:
Y_TRAIN = application_train[target_column]

In [136]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307511 entries, 0 to 307510
Columns: 121 entries, SK_ID_CURR to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: category(16), float64(65), int64(40)
memory usage: 251.0 MB


In [137]:
application_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 48744 entries, 0 to 48743
Columns: 121 entries, SK_ID_CURR to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: category(16), float64(65), int64(40)
memory usage: 39.8 MB


## Итак сделаю препроцессинг для деревьев
    1. Сделаю Кодирование всем текстовым перменным
    2. Сделаю заполнение всех пропущенных данных случайным числом
    3. Запущу и вычеслю лучшие признаки

In [138]:
X_cat = X.select_dtypes(include=['category'])

In [139]:
X_cat.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307511 entries, 0 to 307510
Data columns (total 16 columns):
NAME_CONTRACT_TYPE            307511 non-null category
CODE_GENDER                   307511 non-null category
FLAG_OWN_CAR                  307511 non-null category
FLAG_OWN_REALTY               307511 non-null category
NAME_TYPE_SUITE               306219 non-null category
NAME_INCOME_TYPE              307511 non-null category
NAME_EDUCATION_TYPE           307511 non-null category
NAME_FAMILY_STATUS            307511 non-null category
NAME_HOUSING_TYPE             307511 non-null category
OCCUPATION_TYPE               211120 non-null category
WEEKDAY_APPR_PROCESS_START    307511 non-null category
ORGANIZATION_TYPE             307511 non-null category
FONDKAPREMONT_MODE            97216 non-null category
HOUSETYPE_MODE                153214 non-null category
WALLSMATERIAL_MODE            151170 non-null category
EMERGENCYSTATE_MODE           161756 non-null category
dtypes: ca

In [44]:
X_cat.columns.values

array(['NAME_CONTRACT_TYPE', 'CODE_GENDER', 'FLAG_OWN_CAR',
       'FLAG_OWN_REALTY', 'NAME_TYPE_SUITE', 'NAME_INCOME_TYPE',
       'NAME_EDUCATION_TYPE', 'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE',
       'OCCUPATION_TYPE', 'WEEKDAY_APPR_PROCESS_START',
       'ORGANIZATION_TYPE', 'FONDKAPREMONT_MODE', 'HOUSETYPE_MODE',
       'WALLSMATERIAL_MODE', 'EMERGENCYSTATE_MODE'], dtype=object)

In [52]:
# Посмотрим на наши категории
for cat in X_cat.columns.values:
    print(X_cat.groupby(cat).size(),'\n')

NAME_CONTRACT_TYPE
Cash loans         278232
Revolving loans     29279
dtype: int64 

CODE_GENDER
F      202448
M      105059
XNA         4
dtype: int64 

FLAG_OWN_CAR
N    202924
Y    104587
dtype: int64 

FLAG_OWN_REALTY
N     94199
Y    213312
dtype: int64 

NAME_TYPE_SUITE
Children             3267
Family              40149
Group of people       271
Other_A               866
Other_B              1770
Spouse, partner     11370
Unaccompanied      248526
dtype: int64 

NAME_INCOME_TYPE
Businessman                 10
Commercial associate     71617
Maternity leave              5
Pensioner                55362
State servant            21703
Student                     18
Unemployed                  22
Working                 158774
dtype: int64 

NAME_EDUCATION_TYPE
Academic degree                     164
Higher education                  74863
Incomplete higher                 10277
Lower secondary                    3816
Secondary / secondary special    218391
dtype: int64 

NAME_FAMIL

### Запустим catboost на незаполненых данных и не обработанных категориальных

In [8]:
from catboost import CatBoostClassifier
clf = CatBoostClassifier(eval_metric='AUC')

In [63]:
columns = list(X.columns.values)
columns.remove('SK_ID_CURR')


In [64]:
i=0
index_col = []
for col in columns:
    
    if X_catboost[col].dtype == 'O':
        index_col.append(i)
    i = i+1
index_col    

[0, 1, 2, 3, 9, 10, 11, 12, 13, 26, 30, 38, 84, 85, 87, 88]

In [12]:
clf.fit(X_catboost[columns].values, y, cat_features = index_col)

0:	learn: 0.7006577	total: 734ms	remaining: 12m 13s
1:	learn: 0.7099902	total: 1.42s	remaining: 11m 48s
2:	learn: 0.7136170	total: 2.09s	remaining: 11m 34s
3:	learn: 0.7166641	total: 2.76s	remaining: 11m 26s
4:	learn: 0.7184584	total: 3.41s	remaining: 11m 19s
5:	learn: 0.7194347	total: 4.05s	remaining: 11m 11s
6:	learn: 0.7205659	total: 4.73s	remaining: 11m 10s
7:	learn: 0.7208297	total: 5.41s	remaining: 11m 10s
8:	learn: 0.7209007	total: 6.06s	remaining: 11m 7s
9:	learn: 0.7233819	total: 6.71s	remaining: 11m 3s
10:	learn: 0.7236228	total: 7.36s	remaining: 11m 1s
11:	learn: 0.7241567	total: 8.04s	remaining: 11m 2s
12:	learn: 0.7252343	total: 8.7s	remaining: 11m
13:	learn: 0.7263623	total: 9.35s	remaining: 10m 58s
14:	learn: 0.7266800	total: 10s	remaining: 10m 58s
15:	learn: 0.7267200	total: 10.7s	remaining: 11m
16:	learn: 0.7264462	total: 11.4s	remaining: 11m
17:	learn: 0.7263012	total: 12.1s	remaining: 10m 59s
18:	learn: 0.7275348	total: 12.8s	remaining: 10m 58s
19:	learn: 0.7275315	t

155:	learn: 0.7541650	total: 1m 46s	remaining: 9m 38s
156:	learn: 0.7543080	total: 1m 47s	remaining: 9m 37s
157:	learn: 0.7543756	total: 1m 48s	remaining: 9m 36s
158:	learn: 0.7544610	total: 1m 48s	remaining: 9m 35s
159:	learn: 0.7545143	total: 1m 49s	remaining: 9m 35s
160:	learn: 0.7545882	total: 1m 50s	remaining: 9m 34s
161:	learn: 0.7546441	total: 1m 50s	remaining: 9m 33s
162:	learn: 0.7547381	total: 1m 51s	remaining: 9m 32s
163:	learn: 0.7548158	total: 1m 52s	remaining: 9m 31s
164:	learn: 0.7548657	total: 1m 52s	remaining: 9m 31s
165:	learn: 0.7549418	total: 1m 53s	remaining: 9m 30s
166:	learn: 0.7550146	total: 1m 54s	remaining: 9m 29s
167:	learn: 0.7550674	total: 1m 54s	remaining: 9m 28s
168:	learn: 0.7551444	total: 1m 55s	remaining: 9m 27s
169:	learn: 0.7552503	total: 1m 56s	remaining: 9m 27s
170:	learn: 0.7553103	total: 1m 56s	remaining: 9m 26s
171:	learn: 0.7553789	total: 1m 57s	remaining: 9m 25s
172:	learn: 0.7554660	total: 1m 58s	remaining: 9m 24s
173:	learn: 0.7554760	total:

308:	learn: 0.7612067	total: 3m 34s	remaining: 8m
309:	learn: 0.7612476	total: 3m 35s	remaining: 7m 59s
310:	learn: 0.7612640	total: 3m 36s	remaining: 7m 59s
311:	learn: 0.7613102	total: 3m 36s	remaining: 7m 58s
312:	learn: 0.7613392	total: 3m 37s	remaining: 7m 57s
313:	learn: 0.7613542	total: 3m 38s	remaining: 7m 57s
314:	learn: 0.7613921	total: 3m 39s	remaining: 7m 56s
315:	learn: 0.7614162	total: 3m 39s	remaining: 7m 55s
316:	learn: 0.7614388	total: 3m 40s	remaining: 7m 55s
317:	learn: 0.7614906	total: 3m 41s	remaining: 7m 54s
318:	learn: 0.7615153	total: 3m 41s	remaining: 7m 53s
319:	learn: 0.7615274	total: 3m 42s	remaining: 7m 52s
320:	learn: 0.7615600	total: 3m 43s	remaining: 7m 52s
321:	learn: 0.7615902	total: 3m 43s	remaining: 7m 51s
322:	learn: 0.7616226	total: 3m 44s	remaining: 7m 50s
323:	learn: 0.7616584	total: 3m 45s	remaining: 7m 50s
324:	learn: 0.7617021	total: 3m 46s	remaining: 7m 50s
325:	learn: 0.7617229	total: 3m 47s	remaining: 7m 50s
326:	learn: 0.7617597	total: 3m 

461:	learn: 0.7651408	total: 5m 27s	remaining: 6m 21s
462:	learn: 0.7651602	total: 5m 28s	remaining: 6m 21s
463:	learn: 0.7651739	total: 5m 29s	remaining: 6m 20s
464:	learn: 0.7652010	total: 5m 30s	remaining: 6m 20s
465:	learn: 0.7652251	total: 5m 31s	remaining: 6m 19s
466:	learn: 0.7652607	total: 5m 32s	remaining: 6m 19s
467:	learn: 0.7652954	total: 5m 33s	remaining: 6m 18s
468:	learn: 0.7653127	total: 5m 33s	remaining: 6m 18s
469:	learn: 0.7653279	total: 5m 34s	remaining: 6m 17s
470:	learn: 0.7653411	total: 5m 35s	remaining: 6m 16s
471:	learn: 0.7653588	total: 5m 36s	remaining: 6m 16s
472:	learn: 0.7653682	total: 5m 36s	remaining: 6m 15s
473:	learn: 0.7654039	total: 5m 37s	remaining: 6m 14s
474:	learn: 0.7654102	total: 5m 38s	remaining: 6m 14s
475:	learn: 0.7654352	total: 5m 39s	remaining: 6m 13s
476:	learn: 0.7654766	total: 5m 40s	remaining: 6m 12s
477:	learn: 0.7655004	total: 5m 40s	remaining: 6m 12s
478:	learn: 0.7655140	total: 5m 41s	remaining: 6m 11s
479:	learn: 0.7655328	total:

615:	learn: 0.7682276	total: 7m 25s	remaining: 4m 37s
616:	learn: 0.7682608	total: 7m 26s	remaining: 4m 36s
617:	learn: 0.7682727	total: 7m 26s	remaining: 4m 36s
618:	learn: 0.7683004	total: 7m 27s	remaining: 4m 35s
619:	learn: 0.7683131	total: 7m 28s	remaining: 4m 34s
620:	learn: 0.7683340	total: 7m 28s	remaining: 4m 33s
621:	learn: 0.7683475	total: 7m 29s	remaining: 4m 33s
622:	learn: 0.7683723	total: 7m 30s	remaining: 4m 32s
623:	learn: 0.7683786	total: 7m 31s	remaining: 4m 31s
624:	learn: 0.7683965	total: 7m 31s	remaining: 4m 31s
625:	learn: 0.7684082	total: 7m 32s	remaining: 4m 30s
626:	learn: 0.7684386	total: 7m 33s	remaining: 4m 29s
627:	learn: 0.7684450	total: 7m 34s	remaining: 4m 28s
628:	learn: 0.7684534	total: 7m 34s	remaining: 4m 28s
629:	learn: 0.7684572	total: 7m 35s	remaining: 4m 27s
630:	learn: 0.7684774	total: 7m 36s	remaining: 4m 26s
631:	learn: 0.7684974	total: 7m 37s	remaining: 4m 26s
632:	learn: 0.7685214	total: 7m 37s	remaining: 4m 25s
633:	learn: 0.7685517	total:

768:	learn: 0.7710055	total: 9m 25s	remaining: 2m 49s
769:	learn: 0.7710253	total: 9m 25s	remaining: 2m 49s
770:	learn: 0.7710460	total: 9m 26s	remaining: 2m 48s
771:	learn: 0.7710650	total: 9m 27s	remaining: 2m 47s
772:	learn: 0.7710718	total: 9m 27s	remaining: 2m 46s
773:	learn: 0.7711025	total: 9m 28s	remaining: 2m 46s
774:	learn: 0.7711129	total: 9m 29s	remaining: 2m 45s
775:	learn: 0.7711308	total: 9m 30s	remaining: 2m 44s
776:	learn: 0.7711403	total: 9m 30s	remaining: 2m 43s
777:	learn: 0.7711630	total: 9m 31s	remaining: 2m 43s
778:	learn: 0.7711744	total: 9m 32s	remaining: 2m 42s
779:	learn: 0.7711770	total: 9m 32s	remaining: 2m 41s
780:	learn: 0.7712133	total: 9m 33s	remaining: 2m 40s
781:	learn: 0.7712359	total: 9m 34s	remaining: 2m 40s
782:	learn: 0.7712368	total: 9m 35s	remaining: 2m 39s
783:	learn: 0.7712542	total: 9m 35s	remaining: 2m 38s
784:	learn: 0.7712689	total: 9m 36s	remaining: 2m 37s
785:	learn: 0.7712800	total: 9m 37s	remaining: 2m 37s
786:	learn: 0.7712915	total:

920:	learn: 0.7733813	total: 11m 14s	remaining: 57.9s
921:	learn: 0.7733967	total: 11m 15s	remaining: 57.1s
922:	learn: 0.7734057	total: 11m 16s	remaining: 56.4s
923:	learn: 0.7734077	total: 11m 16s	remaining: 55.7s
924:	learn: 0.7734270	total: 11m 17s	remaining: 54.9s
925:	learn: 0.7734320	total: 11m 18s	remaining: 54.2s
926:	learn: 0.7734458	total: 11m 19s	remaining: 53.5s
927:	learn: 0.7734551	total: 11m 19s	remaining: 52.8s
928:	learn: 0.7734681	total: 11m 20s	remaining: 52s
929:	learn: 0.7734821	total: 11m 21s	remaining: 51.3s
930:	learn: 0.7735036	total: 11m 22s	remaining: 50.6s
931:	learn: 0.7735172	total: 11m 22s	remaining: 49.8s
932:	learn: 0.7735275	total: 11m 23s	remaining: 49.1s
933:	learn: 0.7735378	total: 11m 24s	remaining: 48.3s
934:	learn: 0.7735580	total: 11m 24s	remaining: 47.6s
935:	learn: 0.7735762	total: 11m 25s	remaining: 46.9s
936:	learn: 0.7735822	total: 11m 26s	remaining: 46.1s
937:	learn: 0.7735936	total: 11m 27s	remaining: 45.4s
938:	learn: 0.7736136	total: 1

In [207]:
x, y = (list(x) for x in zip(*sorted(zip(clf.feature_importances_, columns), 
                                                            reverse = False)))
trace2 = go.Bar(
    x=x ,
    y=y,
    marker=dict(
        color=x,
        colorscale = 'Viridis',
        reversescale = True
    ),
    name='Catboost Feature importance',
    orientation='h',
)

layout = dict(
    title='Barplot of Feature importances',
    width = 900, height = 2000,
    yaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=True,
#         domain=[0, 0.85],
    ),
    margin=dict(
    l=200,
),
)

fig1 = go.Figure(data=[trace2])
fig1['layout'].update(layout)
py.iplot(fig1, filename='plots')

In [141]:
Best_Future = []

for future, name in zip(clf.feature_importances_,columns):
    # отберем важность признака больше 0.10
    if future > 0.1:
        Best_Future.append(name)
print(len(Best_Future))        

47


## Посмотрим на лучшие признаки поближе

In [142]:
X_best_fut = X[Best_Future]


In [148]:
X_best_fut['OCCUPATION_TYPE'].mode().values

[Laborers]
Categories (18, object): [Accountants, Cleaning staff, Cooking staff, Core staff, ..., Sales staff, Secretaries, Security staff, Waiters/barmen staff]

In [153]:
X_best_fut['OCCUPATION_TYPE'] = X_best_fut['OCCUPATION_TYPE'].fillna('Laborers')

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [154]:
X_best_fut.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307511 entries, 0 to 307510
Data columns (total 47 columns):
NAME_CONTRACT_TYPE              307511 non-null category
CODE_GENDER                     307511 non-null category
FLAG_OWN_CAR                    307511 non-null category
FLAG_OWN_REALTY                 307511 non-null category
AMT_INCOME_TOTAL                307511 non-null float64
AMT_CREDIT                      307511 non-null float64
AMT_ANNUITY                     307499 non-null float64
AMT_GOODS_PRICE                 307233 non-null float64
NAME_INCOME_TYPE                307511 non-null category
NAME_EDUCATION_TYPE             307511 non-null category
NAME_FAMILY_STATUS              307511 non-null category
NAME_HOUSING_TYPE               307511 non-null category
REGION_POPULATION_RELATIVE      307511 non-null float64
DAYS_BIRTH                      307511 non-null int64
DAYS_EMPLOYED                   307511 non-null int64
DAYS_REGISTRATION               307511 non-nu

In [130]:
X_best_fut.select_dtypes(include = ['category']).columns.values

array(['NAME_CONTRACT_TYPE', 'CODE_GENDER', 'FLAG_OWN_CAR',
       'FLAG_OWN_REALTY', 'NAME_INCOME_TYPE', 'NAME_EDUCATION_TYPE',
       'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'OCCUPATION_TYPE',
       'ORGANIZATION_TYPE'], dtype=object)

In [209]:
## Есть важные признаки Ext Source 3 2 1 для них много признаков но они считаются самыми важными, можно выделить их пропуски 
## и обучить линейную регрессию на заполненых что бы сделать предикт потом на пустых

## Сделаю первый сабмит! Заполню все пропуски средним,Отмасштабирую Числовые, и сделаю кодирование категориальных

In [182]:
from sklearn.preprocessing import  LabelEncoder, LabelBinarizer, OneHotEncoder
from sklearn.pipeline import make_union, make_pipeline
from sklearn.preprocessing import FunctionTransformer, StandardScaler, Imputer
from sklearn.preprocessing import CategoricalEncoder
from sklearn.base import BaseEstimator, TransformerMixin


class Simple_pipeline(BaseEstimator):
    
    def __init__(self, df):
        self.df = df
        
        # Embarked содержит 2 пропуска! Я решил заполнить их самым частым признаком
        # Возможно так делать не корректно но я хотел добавить именно строковый элемент,
        # чтобы можно было преобразовать сразу CategoricalEncoder

    def get_categorical(self, df):
        
        categorical = df.select_dtypes(include=['category']).columns.values  
        
        return df[categorical]

    
    def get_number_future(self, df):
        
        number = df.select_dtypes(include=['number']).columns.values
        
        return df[number]

    
    
    def get_pipline(self):

        pipeline = make_union(*[
            
            
            make_pipeline(FunctionTransformer(self.get_categorical, validate=False),
                          CategoricalEncoder(encoding='ordinal'),Imputer(strategy='most_frequent')),    

            
            make_pipeline(FunctionTransformer(self.get_number_future, validate=False),
                          Imputer(strategy='mean'),StandardScaler())

#             make_pipeline(FunctionTransformer(self.get_object, validate=False),CategoricalEncoder(encoding='ordinal'))
        ])
        
        return pipeline.fit_transform(self.df)

In [208]:
X_Pipline = Simple_pipeline(X_best_fut).get_pipline()

/anaconda3/lib/python3.6/site-packages/sklearn/utils/deprecation.py:58: DeprecationWarning:

Class Imputer is deprecated; Imputer was deprecated in version 0.20 and will be removed in 0.22. Import impute.SimpleImputer from sklearn instead.

/anaconda3/lib/python3.6/site-packages/sklearn/utils/deprecation.py:58: DeprecationWarning:

Class Imputer is deprecated; Imputer was deprecated in version 0.20 and will be removed in 0.22. Import impute.SimpleImputer from sklearn instead.



In [185]:
import lightgbm as lgb
model = lgb.LGBMClassifier()

In [187]:
X_Pipline.shape,y.shape

(307511, 47)

In [193]:
np.mean(cross_val_score(model, X_Pipline, y, cv=5, scoring='roc_auc'))

0.7560352268558159

### Создадим несколько дефолтных моделек и посмотрим на их качество

In [194]:
# Class to extend the Sklearn classifier
class SklearnHelper(object):
    def __init__(self, mod, seed=0, params=None):
        
        self.mod = mod()

    def train(self, x_train, y_train):
        self.mod.fit(x_train, y_train)
        
    def cros_val_score(self,x_train,y_train):
        
        score = np.mean(cross_val_score(self.mod, x_train, y_train, cv=5, scoring='roc_auc'))
        print(self.mod.__class__,score)

    def predict(self, x):
        return self.mod.predict(x)
    
    def fit(self,x,y):
        return self.mod.fit(x,y)
    
    def feature_importances(self,x,y):
        print(self.mod.fit(x,y).feature_importances_)

In [272]:
# Create 5 objects that represent our 4 models
rf = SklearnHelper(mod=RandomForestClassifier)
et = SklearnHelper(mod=ExtraTreesClassifier)
ada = SklearnHelper(mod=AdaBoostClassifier)
gb = SklearnHelper(mod=GradientBoostingClassifier)
svc = SklearnHelper(mod=SVC)

In [ ]:
for model in [knn,lr,gbm,gnb,dtree]:
    score = model.cros_val_score(X_Pipline,Y_TRAIN)
    print(model.__class__,score)

In [209]:
knn = SklearnHelper(mod=KNeighborsClassifier)
lr = SklearnHelper(mod=LogisticRegression)
gbm = SklearnHelper(mod=XGBClassifier)
gnb = SklearnHelper(mod=GaussianNB)
dtree = SklearnHelper(mod=DecisionTreeClassifier)

## Так хорошо! Теперь посмотрю какие признаки можно сгенерировать!
## Exit1,Exit2,Exit3
    1. Заполню основные признаки значениями из предсказаний линейной регрессии

In [219]:
X_best_fut.select_dtypes(include = ['number']).columns.values

array(['AMT_INCOME_TOTAL', 'AMT_CREDIT', 'AMT_ANNUITY', 'AMT_GOODS_PRICE',
       'REGION_POPULATION_RELATIVE', 'DAYS_BIRTH', 'DAYS_EMPLOYED',
       'DAYS_REGISTRATION', 'DAYS_ID_PUBLISH', 'OWN_CAR_AGE',
       'FLAG_EMP_PHONE', 'FLAG_WORK_PHONE', 'CNT_FAM_MEMBERS',
       'REGION_RATING_CLIENT_W_CITY', 'HOUR_APPR_PROCESS_START',
       'REG_CITY_NOT_LIVE_CITY', 'EXT_SOURCE_1', 'EXT_SOURCE_2',
       'EXT_SOURCE_3', 'APARTMENTS_AVG', 'YEARS_BEGINEXPLUATATION_AVG',
       'FLOORSMAX_AVG', 'YEARS_BEGINEXPLUATATION_MODE', 'APARTMENTS_MEDI',
       'YEARS_BEGINEXPLUATATION_MEDI', 'TOTALAREA_MODE',
       'OBS_30_CNT_SOCIAL_CIRCLE', 'DEF_30_CNT_SOCIAL_CIRCLE',
       'OBS_60_CNT_SOCIAL_CIRCLE', 'DEF_60_CNT_SOCIAL_CIRCLE',
       'DAYS_LAST_PHONE_CHANGE', 'FLAG_DOCUMENT_3', 'FLAG_DOCUMENT_16',
       'FLAG_DOCUMENT_18', 'AMT_REQ_CREDIT_BUREAU_MON',
       'AMT_REQ_CREDIT_BUREAU_QRT', 'AMT_REQ_CREDIT_BUREAU_YEAR'],
      dtype=object)

In [221]:
linear_col = X_best_fut.select_dtypes(include = ['number']).columns.values

In [224]:
# Из отчета видно что 3 главных признака идут от 0 до 1! Можно предположить что они являются комбинацией других признаков

In [233]:
X_linear_mod = X_best_fut[linear_col]
pd.set_option('display.max_columns', 500)
X_linear_mod.head()

AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
0          202500.0    406597.5      24700.5         351000.0   
1          270000.0   1293502.5      35698.5        1129500.0   
2           67500.0    135000.0       6750.0         135000.0   
3          135000.0    312682.5      29686.5         297000.0   
4          121500.0    513000.0      21865.5         513000.0   

   REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  \
0                    0.018801       -9461           -637            -3648.0   
1                    0.003541      -16765          -1188            -1186.0   
2                    0.010032      -19046           -225            -4260.0   
3                    0.008019      -19005          -3039            -9833.0   
4                    0.028663      -19932          -3038            -4311.0   

   DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
0            -2120          NaN               1                0   
1             -291          NaN               1                0   
2            -2531         26.0               1                1   
3            -2437          NaN               1                0   
4            -3458          NaN               1                0   

   CNT_FAM_MEMBERS  REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
0              1.0                            2                       10   
1              2.0                            1                       11   
2              1.0                            2                        9   
3              2.0                            2                       17   
4              1.0                            2                       11   

   REG_CITY_NOT_LIVE_CITY  EXT_SOURCE_1  EXT_SOURCE_2  EXT_SOURCE_3  \
0                       0      0.083037      0.262949      0.139376   
1                       0      0.311267      0.622246           NaN   
2                       0           NaN      0.555912      0.729567   
3                       0           NaN      0.650442           NaN   
4                       0           NaN      0.322738           NaN   

   APARTMENTS_AVG  YEARS_BEGINEXPLUATATION_AVG  FLOORSMAX_AVG  \
0          0.0247                       0.9722         0.0833   
1          0.0959                       0.9851         0.2917   
2             NaN                          NaN            NaN   
3             NaN                          NaN            NaN   
4             NaN                          NaN            NaN   

   YEARS_BEGINEXPLUATATION_MODE  APARTMENTS_MEDI  \
0                        0.9722           0.0250   
1                        0.9851           0.0968   
2                           NaN              NaN   
3                           NaN              NaN   
4                           NaN              NaN   

   YEARS_BEGINEXPLUATATION_MEDI  TOTALAREA_MODE  OBS_30_CNT_SOCIAL_CIRCLE  \
0                        0.9722          0.0149                       2.0   
1                        0.9851          0.0714                       1.0   
2                           NaN             NaN                       0.0   
3                           NaN             NaN                       2.0   
4                           NaN             NaN                       0.0   

   DEF_30_CNT_SOCIAL_CIRCLE  OBS_60_CNT_SOCIAL_CIRCLE  \
0                       2.0                       2.0   
1                       0.0                       1.0   
2                       0.0                       0.0   
3                       0.0                       2.0   
4                       0.0                       0.0   

   DEF_60_CNT_SOCIAL_CIRCLE  DAYS_LAST_PHONE_CHANGE  FLAG_DOCUMENT_3  \
0                       2.0                 -1134.0                1   
1                       0.0                  -828.0                1   
2                       0.0                  -815.0                0   
3                       0.0                  -

In [234]:
X_linear_mod.shape

(307511, 37)

In [235]:
y_linear_exit3 = X_linear_mod['EXT_SOURCE_3']
X_linear_mod.drop(['EXT_SOURCE_3','EXT_SOURCE_2','EXT_SOURCE_1'],axis = 1,inplace = True)

/anaconda3/lib/python3.6/site-packages/pandas/core/frame.py:3694: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [236]:
X_linear_mod.shape

(307511, 34)

In [248]:
index_nan = []
i = 0
for nan in y_linear_exit3.isna():
    
    if nan  == True:
        index_nan.append(i)
    i = i+1 
len(index_nan)    

60965

In [267]:
X_linear_mod_test = X_linear_mod.loc[index_nan]
X_linear_mod_train = X_linear_mod.drop(index=index_nan)

In [278]:
y_linear_train = y_linear_exit3.loc[X_linear_mod_train.index]

In [279]:
y_linear_train

0         0.139376
2         0.729567
5         0.621226
6         0.492060
7         0.540654
8         0.751724
10        0.363945
11        0.652897
12        0.176653
13        0.770087
15        0.678568
16        0.062103
18        0.556727
19        0.477649
21        0.542445
22        0.358951
23        0.669057
24        0.565608
25        0.461482
26        0.190706
27        0.659406
28        0.524496
30        0.410103
32        0.798137
33        0.411849
35        0.678568
36        0.754406
37        0.722393
38        0.751724
39        0.605836
            ...   
307476    0.771362
307477    0.667458
307478    0.420611
307479    0.352340
307480    0.647977
307481    0.511892
307482    0.394495
307483    0.520898
307485    0.865896
307486    0.199771
307487    0.255332
307488    0.529890
307489    0.397946
307490    0.495666
307491    0.716570
307492    0.365617
307493    0.728141
307494    0.511892
307495    0.597192
307496    0.486653
307497    0.524496
307498    0.

In [261]:
X_linear_mod_train.shape

(246546, 34)

In [249]:
X_linear_mod_test.shape

(60965, 34)

### Создадим Пайплан для заполнения пропусков предсказаними линейкой

In [266]:
from sklearn.preprocessing import  LabelEncoder, LabelBinarizer, OneHotEncoder
from sklearn.pipeline import make_union, make_pipeline
from sklearn.preprocessing import FunctionTransformer, StandardScaler, Imputer
from sklearn.preprocessing import CategoricalEncoder
from sklearn.base import BaseEstimator, TransformerMixin


class Liner_pred_pipeline(BaseEstimator):
    
    def __init__(self, df):
        self.df = df
        
        # Embarked содержит 2 пропуска! Я решил заполнить их самым частым признаком
        # Возможно так делать не корректно но я хотел добавить именно строковый элемент,
        # чтобы можно было преобразовать сразу CategoricalEncoder

    def get_df(self, df):
          
        return df

    

    
    
    def get_pipline(self):

        pipeline = make_union(*[
            
            
            make_pipeline(FunctionTransformer(self.get_df, validate=False),
                          Imputer(strategy='mean'),
                          StandardScaler())   

        ])
        
        return pipeline.fit_transform(self.df)

In [268]:
XL_train = Liner_pred_pipeline(X_linear_mod_train).get_pipline()

/anaconda3/lib/python3.6/site-packages/sklearn/utils/deprecation.py:58: DeprecationWarning:

Class Imputer is deprecated; Imputer was deprecated in version 0.20 and will be removed in 0.22. Import impute.SimpleImputer from sklearn instead.



In [265]:
from sklearn.linear_model import LinearRegression
lin_reg = LinearRegression()

In [ ]:
x_train, x_valid, y_train, y_valid = train_test_split(XL_train, y_linear_train,
                                                    test_size=0.3, stratify=y_linear_train, random_state=17)

In [ ]:
lin_reg.fit(XL_train,y_linear_train)